# Lab setup

This tutorial walks through the process of setting up a lab and the related chemical inventory, vessels, experiment template components, etc.

First, we log into the server. In this case we are logging into a local instance of ESCALATE

In [90]:
import os
import sys
module_path = os.path.abspath(os.path.join('../../'))
if module_path not in sys.path:
    sys.path.append(module_path)
import escalateclient
import importlib

In [91]:
importlib.reload(escalateclient)
server_url = 'http://localhost:8000'
username = 'vshekar'
password = 'copperhead123'
client = escalateclient.ESCALATEClient(server_url, username, password)

Next, we set up organizations (they can be hierarchical). For example, we can create Neilson lab under University of Colorado

In [92]:
# Creating University of Colorado first
cu_info = { "description": "University of Colorado",
            "full_name": "University of Colorado at Boulder",
            "short_name": "CU",
            "address1": "Boulder, CO 80309",
            "address2": "",
            "city": "Boulder",
            "state_province": "CO",
            "zip": "80309",
            "country": "USA",
            "phone": '123456',
            "website_url": 'www.colorado.edu',
            }

cu_response = client.get_or_create(endpoint='organization', data=cu_info)
#cu_response = client.get(endpoint='organization', data=cu_info)
print(cu_response)

{'description': 'University of Colorado', 'full_name': 'University of Colorado at Boulder', 'short_name': 'CU', 'address1': 'Boulder, CO 80309', 'city': 'Boulder', 'state_province': 'CO', 'zip': '80309', 'country': 'USA', 'phone': '123456', 'website_url': 'www.colorado.edu'}
GET: OK. Found 1 results
[{'url': 'http://localhost:8000/api/organization/09e2eefd-1b84-458f-b6dd-6b027753f3a5/', 'uuid': '09e2eefd-1b84-458f-b6dd-6b027753f3a5', 'edocs': [], 'tags': [], 'notes': [], 'address1': 'Boulder, CO 80309', 'address2': '', 'city': 'Boulder', 'state_province': 'CO', 'zip': '80309', 'country': 'USA', 'phone': '123456', 'add_date': '2022-06-27T18:54:32.245719', 'mod_date': '2022-06-27T18:54:32.245751', 'description': 'University of Colorado', 'full_name': 'University of Colorado at Boulder', 'short_name': 'CU', 'website_url': 'www.colorado.edu', 'parent_path': None, 'internal_slug': 'university-of-colorado-at-boulder-cu', 'parent': None}]


In [6]:
# Then creating the Neilson Lab
neilson_lab_data = { 
    'description': 'Neilson Lab', 
    'address1': 'Boulder, CO 80309', 
    'address2': '', 
    'city': 'Boulder', 
    'state_province': 'CO', 
    'zip': '80309', 
    'country': 'USA', 
    'phone': '123456',
    'full_name': 'Neilson Lab', 
    'short_name': 'NL', 
    'website_url': 'www.colorado.edu', 
    'parent': cu_response[0]['url']}

nl_response = client.get_or_create(endpoint='organization', data=neilson_lab_data)

# Creating a person entry to identify the owner
# Note: If a user account is created, a person entry is automatically created for that user

neilson_data = {
    "first_name": "James",
    "middle_name": "",
    "last_name": "Neilson",
    "address1": "",
    "address2": "",
    "city": "",
    "state_province": "",
    "zip": "",
    "country": "",
    "phone": "",
    "email": "",
    "title": "",
    "suffix": "",
    "organization": cu_response[0]['url']
}

neilson_response = client.get_or_create('person', data=neilson_data)
neilson_actor = client.get('actor', data={'person': neilson_response[0]['url']})

{'description': 'Neilson Lab', 'address1': 'Boulder, CO 80309', 'city': 'Boulder', 'state_province': 'CO', 'zip': '80309', 'country': 'USA', 'phone': '123456', 'full_name': 'Neilson Lab', 'short_name': 'NL', 'website_url': 'www.colorado.edu', 'parent': '09e2eefd-1b84-458f-b6dd-6b027753f3a5'}
GET: OK. Found 0 results
POST: OK, returning new resource dict
{'first_name': 'James', 'last_name': 'Neilson', 'organization': '09e2eefd-1b84-458f-b6dd-6b027753f3a5'}
GET: OK. Found 0 results
POST: OK, returning new resource dict
{'person': '1074acc8-4beb-4638-8801-05324bd4c9c2'}
GET: OK. Found 1 results


Next, we set up an inventory for the lab

In [93]:
# Get value, get always returns a list, even if there is only one element to be returned
active_status = client.get_or_create(endpoint='status', data={'description': 'active'})

# Inventory details
nl_inventory = {
    "description": "Nielson Lab Inventory",
    "status": active_status[0]['url'], # Indicates active status
    "actor": neilson_actor[0]['url'],
    "owner": neilson_actor[0]['url'], # Indicates James Neilson as owner
    "operator": neilson_actor[0]['url'], # Indicates James Neilson as operator
    "lab": neilson_actor[0]['url'] # Associates inventory with Neilson Lab
}

nl_inventory_response = client.get_or_create(endpoint='inventory', data=nl_inventory)

{'description': 'active'}
GET: OK. Found 1 results
{'description': 'Nielson Lab Inventory', 'status': 'f105cba7-c77b-434f-9126-7f0908995fde', 'actor': '26969748-2725-465e-95e1-17f76b50a3a0', 'owner': '26969748-2725-465e-95e1-17f76b50a3a0', 'operator': '26969748-2725-465e-95e1-17f76b50a3a0', 'lab': '26969748-2725-465e-95e1-17f76b50a3a0'}
GET: OK. Found 1 results


# Materials

Once the inventory is set up we can add chemicals (materials) to it. At the bare minimum, all we need to input is a description (e.g. name) for each chemical. However, depending on our intent for use of ESCALATE we might want to add more information for each material. The easiest way to do this is to load from a .csv file that contains all the desired information.

In [94]:
import pandas as pd 
chem_list = pd.read_csv('Chemicals List.csv')
chem_list = chem_list.fillna('')
chem_list['Material type'] = chem_list['Material type'].str.replace('Gas', 'flux')

chem_list.head()

BarCode Chemical Name Inventory Name     CAS Num   Phase Purity  \
0  120585         Argon                  7440-37-1     Gas          
1  128224       Benzene                    71-43-2  Liquid          
2   20790    Boric acid                 10043-35-3   Solid          
3  207298      Chromium         Powder   7440-47-3   Solid          
4   23852        Cobalt   metal powder   7440-48-4   Solid          

        Vendor Material type  molar mass  
0  CSU Legacy           flux       39.95  
1  CSU Legacy        Organic       78.11  
2  CSU Legacy        Organic       61.83  
3  CSU Legacy      Inorganic       51.99  
4  CSU Legacy      Inorganic       58.93

In this example our .csv file contains the CAS number, phase, material type, and molar mass of each chemical. Below we add each of the materials to the database, then load them into the inventory. At the material level, we associate the material type (a field in the materials table) and molar mass (a material property). At the inventory material level, we associate the CAS number (aka part no) and phase - both are fields in that table.

In [95]:
for i, row in chem_list.iterrows():
    chemical_name = row['Chemical Name']
    material_types = row['Material type'].lower().split(',')
    mt_responses = []
    for mt in material_types:
        mt_responses.append(client.get_or_create('material-type', data={'description': mt})[0]) # Get material type from a separate database table
    # Add material to db
    material_data = {'description': chemical_name, 'material_type': [mtr['url'] for mtr in mt_responses], 'material_class':'model'}
    material_response = client.get_or_create('material', data=material_data)
    # Add material to inventory
    if row['Inventory Name']:
        description = f"{chemical_name} {row['Inventory Name']}"
    else:
        description = chemical_name
    im_data = {
        "description": description,
        "part_no": f"{row['CAS Num']}",
        "phase": row['Phase'].lower(),
        "inventory": nl_inventory_response[0]['url'], #Associates inventory material with Neilson lab inventory
        "material": material_response[0]['url'] #Associates inventory material with material
    }
    im_response = client.get_or_create('inventory-material', data=im_data)

{'description': 'flux'}
GET: OK. Found 1 results
{'description': 'Argon', 'material_type': ['http://localhost:8000/api/material-type/d206685a-122c-4c68-b7ab-328e4cbb5175/'], 'material_class': 'model'}
GET: OK. Found 0 results
POST: OK, returning new resource dict
{'description': 'Argon', 'part_no': '7440-37-1', 'phase': 'gas', 'inventory': 'a2d51de7-2e8a-468c-b0d4-ffc1e7b2da01', 'material': '3e9979fa-4649-43f1-b0bb-42454efe564f'}
GET: OK. Found 0 results
POST: OK, returning new resource dict
{'description': 'organic'}
GET: OK. Found 1 results
{'description': 'Benzene', 'material_type': ['http://localhost:8000/api/material-type/7b0228e0-96eb-4c57-b43f-4e940020096d/'], 'material_class': 'model'}
GET: OK. Found 0 results
POST: OK, returning new resource dict
{'description': 'Benzene', 'part_no': '71-43-2', 'phase': 'liquid', 'inventory': 'a2d51de7-2e8a-468c-b0d4-ffc1e7b2da01', 'material': 'c1c21a3a-c937-4b27-8392-84525b517cbb'}
GET: OK. Found 0 results
POST: OK, returning new resource dic

In [96]:
# Get or create property definition for molar mass
property_data={'description':'Molecular weight', 'property_def_class': 'intrinsic'}
property_template_response = client.get_or_create('property-template', data=property_data)

#Add molar mass property to materials 
for i, material in enumerate(chem_list['Chemical Name']):
    material_data={'description': material}
    material_response = client.get('material', data=material_data)
    mw = chem_list['molar mass'][i]
    
    data = {
    'value': {'value': float(mw), 'unit': 'g/mol', 'type': 'num'},
    'material': material_response[0]['url'],
    'template': property_template_response[0]['url']
}
    client.post('property', data)

{'description': 'Molecular weight', 'property_def_class': 'intrinsic'}
GET: OK. Found 0 results
POST: OK, returning new resource dict
{'description': 'Argon'}
GET: OK. Found 4 results
POST: FAILED, returning response object
Status 500: Internal Server Error <!DOCTYPE html>
<html lang="en">
<head>
  <meta http-equiv="content-type" content="text/html; charset=utf-8">
  <meta name="robots" content="NONE,NOARCHIVE">
  <title>KeyError
          at /api/property/</title>
  <style type="text/css">
    html * { padding:0; margin:0; }
    body * { padding:10px 20px; }
    body * * { padding:0; }
    body { font:small sans-serif; background-color:#fff; color:#000; }
    body>div { border-bottom:1px solid #ddd; }
    h1 { font-weight:normal; }
    h2 { margin-bottom:.8em; }
    h3 { margin:1em 0 .5em 0; }
    h4 { margin:0 0 .5em 0; font-weight: normal; }
    code, pre { font-size: 100%; white-space: pre-wrap; }
    table { border:1px solid #ccc; border-collapse: collapse; width:100%; background:

For clarity, here is a breakdown of the various database fields that can be associated with chemicals, at the material level and the inventory level. Again, only descriptions are required, but including other fields makes it easier to work with ESCALATE

**Material fields**
* material type (e.g. "organic")
* material identifier (e.g. "molecular formula")
* material property (e.g. "density", "molecular weight")

**Inventory material fields**
* phase (e.g. "solid")
* part no. (e.g. "CAS Number")

The fields at the material level link to other database tables. for instance, there are database entries for different material types. That means that these fields from other tables must be accessed first and then associated with the material. In the event that a particular entry does not exist in the associated table, it must be created.

At the inventory material level, the listed fields are string descriptions.

# Vessels

Like chemicals, vessels can be added to the database from a .csv file.

In [97]:
vessels_list = pd.read_csv('load_opentrons_vessels.csv')
vessels_list = vessels_list.fillna('')
vessels_list.head()

description total_volume  well_number column_order
0    biorad_96_wellplate_200ul_pcr       200 uL           96             
1  corning_12_wellplate_6.9ml_flat       6.9 mL           12             
2  corning_24_wellplate_3.4ml_flat       3.4 mL           24             
3  corning_48_wellplate_1.6ml_flat       1.6 mL           48             
4  corning_6_wellplate_16.8ml_flat      16.8 mL            6

Here we are going to add a description, volume capacity ("total volume"), well count ("well number"), and column order (useful for liquid-handling experiments involving robots) for each vessel. Like for materials, only a description is required, but adding more information can be helpful depending on how you plan to use the software.

In [98]:
for i, row in vessels_list.iterrows():
    vessel_name = row['description']
    vol = row["total_volume"]
    #Enter volume as a value field
    if len(vol.split()) > 1:
        val = vol.split()[0]
        unit = vol.split()[1]
        total_volume = {"value": val, "unit": unit, "type": "num"}
    else:
        total_volume = None
    
    well_number = row["well_number"]
    column_order = row["column_order"]

    vessel_data = {'description': vessel_name,
                    'total_volume': total_volume,
                    'well_number': well_number,
                    'column_order': column_order,
                    'status': active_status[0]['url'],
                    }
    # Add vessel data to db
    vessel_response = client.get_or_create('vessel', data=vessel_data)

{'description': 'biorad_96_wellplate_200ul_pcr', 'well_number': 96, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: OK. Found 1 results
{'description': 'corning_12_wellplate_6.9ml_flat', 'well_number': 12, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: OK. Found 1 results
{'description': 'corning_24_wellplate_3.4ml_flat', 'well_number': 24, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: OK. Found 1 results
{'description': 'corning_48_wellplate_1.6ml_flat', 'well_number': 48, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: OK. Found 1 results
{'description': 'corning_6_wellplate_16.8ml_flat', 'well_number': 6, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: OK. Found 1 results
{'description': 'corning_6_wellplate_16.8ml_flat', 'well_number': 96, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: OK. Found 1 results
{'description': 'nest_96_wellplate_100ul_pcr_full_skirt', 'well_number': 96, 'status': 'f105cba7-c77b-434f-9126-7f0908995fde'}
GET: O

# Properties, Actions, and Parameters

Next, we check to make sure the database contains the property definitions, action definitions and parameters we'll need. This ensures that we have all the pieces necessary to create experiment templates seamlessly - but we can always go back and add missing definitions later during the template creation process if we forget any

In [99]:
#Print a list of existing action definitions
for action_def in client.get('action-def'):
    print(action_def['description'])

{}
GET: OK. Found 8 results
heat
heat_stir
stir
dispense
bring_to_temperature
dispense_solid
dwell
cool


In [100]:
#Add new action definition
params = client.get_or_create('parameter-def', data={'description': 'temperature'}) #Get parameter def from a separate database table

client.post('action-def', data={'description': 'cool', 'parameter_def': params[0]['url']})

{'description': 'temperature'}
GET: OK. Found 1 results
POST: FAILED, returning response object
Status 400: Bad Request {"description":["action def with this description already exists."],"parameter_def":["Expected a list of items but got type \"str\"."]}


<Response [400]>